# 🏠 Necesidad de vivienda en Villa Unión

In [1]:
## ---- Librerias ---- ##
# --- Librerías únicas y ordenadas ---
import sys
import numpy as np
import pandas as pd
from difflib import get_close_matches
import re
from collections import Counter
import matplotlib.pyplot as plt
from geopy.distance import geodesic
import folium


sys.path.append('../Funciones')

from funciones import  DF_CLAVES, leer_archivo, obtener_establecimientos_localidad, obtener_claves_estado_mun, analizar_columnas,comercios, categorias_establecimientos

In [ ]:
## ---- Definicion de funciones ---- ##
def corregir_nombres_estado_municipio(estado, municipio):
    """
    Normaliza nombres de estado y municipio usando las claves oficiales.

    Parámetros:
    ------------
    estado : str
    municipio : str

    Retorna:
    --------
    estado_normalizado, municipio_normalizado : tuple[str, str]
        Los nombres corregidos y en formato oficial según DF_CLAVES.
    
    Lanza:
    ------
    ValueError si hay errores ortográficos que no pueden corregirse.
    """
    estado = estado.strip().title()
    municipio = municipio.strip().title()

    entidades = DF_CLAVES['NOM_ENT'].unique()
    if estado not in entidades:
        sugerencia = get_close_matches(estado, entidades, n=1, cutoff=0.6)
        raise ValueError(f"Estado no encontrado. ¿Quisiste decir '{sugerencia[0]}'?" if sugerencia else f"'{estado}' no es un estado válido.")

    df_ent = DF_CLAVES[DF_CLAVES['NOM_ENT'] == estado]
    municipios = df_ent['NOM_MUN'].unique()
    if municipio not in municipios:
        sugerencia = get_close_matches(municipio, municipios, n=1, cutoff=0.6)
        raise ValueError(f"Municipio no encontrado. ¿Quisiste decir '{sugerencia[0]}'?" if sugerencia else f"'{municipio}' no está en el estado '{estado}'.")

    # Recuperar nombres corregidos (como aparecen en el archivo oficial)
    estado_corregido = df_ent['NOM_ENT'].iloc[0]
    municipio_corregido = df_ent[df_ent['NOM_MUN'] == municipio]['NOM_MUN'].iloc[0]
    return estado_corregido, municipio_corregido

def dms_a_decimal(coord):
    import re

    # Validar entrada
    if pd.isna(coord):
        return None

    coord = str(coord).strip()

    # Buscar grados, minutos, segundos y dirección
    match = re.match(r"(\d+)°(\d+)'([\d\.]+)\"?\s*([NSEW])", coord)
    if not match:
        return None  # formato inválido

    grados, minutos, segundos, direccion = match.groups()
    decimal = float(grados) + float(minutos)/60 + float(segundos)/3600

    if direccion in ['S', 'W']:
        decimal *= -1

    return decimal

def construir_df(
    df_2020, df_2010, df_2005, df_2000, df_1995, df_1990,
    col_2020, col_2010, col_2005, col_2000, col_1995, col_1990,
    estado, municipio
):
    pob_sin = df_2020[df_2020['NOM_ENT'] == estado][col_2020].iloc[0]
    pob_maza = df_2020[(df_2020['NOM_MUN'] == municipio) & (df_2020['NOM_LOC'] == municipio)][col_2020].iloc[0]
    pob_villa_u = df_2020[(df_2020['NOM_MUN'] == municipio) & (df_2020['NOM_LOC'] == 'Villa Unión')][col_2020].iloc[0]

    pob_sin_2010 = df_2010[df_2010['nom_ent'] == estado][col_2010].iloc[0]
    pob_maza_2010 = df_2010[(df_2010['nom_mun'] == municipio) & (df_2010['nom_loc'] == municipio)][col_2010].iloc[0]
    pob_villa_u_2010 = df_2010[(df_2010['nom_mun'] == municipio) & (df_2010['nom_loc'] == 'Villa Unión')][col_2010].iloc[0]

    pob_sin_2005 = df_2005[df_2005['nom_ent'] == estado][col_2005].iloc[0]
    pob_maza_2005 = df_2005[(df_2005['nom_mun'] == municipio) & (df_2005['nom_loc'] == municipio)][col_2005].iloc[0]
    pob_villa_u_2005 = df_2005[(df_2005['nom_mun'] == municipio) & (df_2005['nom_loc'] == 'Villa Unión')][col_2005].iloc[0]

    pob_sin_2000 = df_2000[df_2000['nom_ent'] == estado][col_2000].iloc[0]
    pob_maza_2000 = df_2000[(df_2000['nom_mun'] == municipio) & (df_2000['nom_loc'] == 'MAZATLAN')][col_2000].iloc[0]
    pob_villa_u_2000 = df_2000[(df_2000['nom_mun'] == municipio) & (df_2000['nom_loc'] == 'VILLA UNION')][col_2000].iloc[0]

    pob_sin_1995 = df_1995[df_1995['NOM_ENT\t'] == estado][col_1995].iloc[0]
    pob_maza_1995 = df_1995[(df_1995['NOM_MUN\t'] == municipio) & (df_1995['NOM_LOC\t'] == 'MAZATLAN')][col_1995].iloc[0]
    pob_villa_u_1995 = df_1995[(df_1995['NOM_MUN\t'] == municipio) & (df_1995['NOM_LOC\t'] == 'VILLA UNION')][col_1995].iloc[0]

    pob_sin_1990 = df_1990[df_1990['NOM_ENT\t'] == estado][col_1990].iloc[0]
    pob_maza_1990 = df_1990[(df_1990['NOM_MUN\t'] == municipio) & (df_1990['NOM_LOC\t'] == 'MAZATLAN')][col_1990].iloc[0]
    pob_villa_u_1990 = df_1990[(df_1990['NOM_MUN\t'] == municipio) & (df_1990['NOM_LOC\t'] == 'VILLA UNION')][col_1990].iloc[0]

    df = pd.DataFrame({
        'Año': [1990, 1995, 2000, 2005, 2010, 2020],
        'Población Sinaloa': [pob_sin_1990, pob_sin_1995, pob_sin_2000, pob_sin_2005, pob_sin_2010, pob_sin],
        'Población Mazatlán': [pob_maza_1990, pob_maza_1995, pob_maza_2000, pob_maza_2005, pob_maza_2010, pob_maza],
        'Población Villa Unión': [pob_villa_u_1990, pob_villa_u_1995, pob_villa_u_2000, pob_villa_u_2005, pob_villa_u_2010, pob_villa_u]
    })
    return df

# Seleccionar el estado y municipio para el modelo
# Seleccionar el estado y municipio para el modelo
estado = "Sinaloa"
municipio = "mazatlán"

# Obtener 'CVE_ENT' y 'CVE_MUN' 
claves= obtener_claves_estado_mun(estado,municipio,retornar_resultado=True)

estado, municipio = corregir_nombres_estado_municipio(estado, municipio)

## ---- Extraccion de datos ---- ##

# Datos todo el Municipio de Mazatlán 2020
df_2020_completo = leer_archivo("C:/Users/julio/OneDrive/Documentos/Trabajo/IdeasFrscas/Proyecto Villa Union/Base de datos/Sinaloa_2020.csv")
df_mun_tot = df_2020_completo.copy()#[df_2020_completo['NOM_MUN']==municipio].copy()

# Datos todo el Municipio de Mazatlán 2010
df_2010_completo = leer_archivo("C:/Users/julio/OneDrive/Documentos/Trabajo/IdeasFrscas/Proyecto Villa Union/Base de datos/Sinaloa_2010.csv")
df_mun_tot_2010 = df_2010_completo.copy()#[df_2010_completo['nom_mun']==municipio].copy()

# Datos todo el Municipio de Mazatlán 2005
df_2005_completo = leer_archivo("C:/Users/julio/OneDrive/Documentos/Trabajo/IdeasFrscas/Proyecto Villa Union/Base de datos/Sinaloa_2005.csv")
df_mun_tot_2005 = df_2005_completo.copy()#[df_2005_completo['nom_mun']==municipio].copy()

# Importar la base de datos de la población 2000 por ITER
ruta_2000= f"C:/Users/julio/OneDrive/Documentos/Trabajo/Ideas Frescas/Bases de datos/Censo Poblacion y Vivienda/Resultado por ITER/cgpv2000_iter_{claves['CVE_ENT']}.csv"
df_2000 = leer_archivo(ruta_2000)

# Importar la base de datos de la población 1995 por ITER
ruta_1995= f"C:/Users/julio/OneDrive/Documentos/Trabajo/Ideas Frescas/Bases de datos/Censo Poblacion y Vivienda/Resultado por ITER/ITER_{claves['CVE_ENT']}XLS95.xls"
df_1995 = leer_archivo(ruta_1995)

# Importar la base de datos de la población 1990 por ITER
ruta_1990= f"C:/Users/julio/OneDrive/Documentos/Trabajo/Ideas Frescas/Bases de datos/Censo Poblacion y Vivienda/Resultado por ITER/ITER_{claves['CVE_ENT']}XLS90.xls"
df_1990 = leer_archivo(ruta_1990)




## ----- Limpieza de datos ------ ##

# Analizar carecteres raros dentro de la base de datos 2020

# Selecciona las columnas numericas a partir de la columna 7 para hacer el analisis
sub_df = df_mun_tot.iloc[:, 9:].astype(str)

# Inicializa una lista para almacenar caracteres raros
caracteres_raros = []

# Recorre cada columna y cada valor
for col in sub_df.columns:
    for valor in sub_df[col]:
        encontrados = re.findall(r'[^0-9\.\-]', valor)  # Excluye dígitos, punto y guion
        caracteres_raros.extend(encontrados)

# Contar ocurrencias totales
conteo_caracteres = Counter(caracteres_raros)

# Mostrar resultados
#print("Caracteres no numéricos encontrados en todo el DataFrame:", list(conteo_caracteres.keys()))
#print("Frecuencias:", conteo_caracteres)


# ----- Analizar carecteres raros dentro de la base de datos 2010 ------- #

# Selecciona las columnas numericas a partir de la columna 7 para hacer el analisis
sub_df_2010 = df_mun_tot_2010.iloc[:, 9:].astype(str)

# Inicializa una lista para almacenar caracteres raros
caracteres_raros_2010 = []

# Recorre cada columna y cada valor
for col in sub_df_2010.columns:
    for valor in sub_df_2010[col]:
        encontrados = re.findall(r'[^0-9\.\-]', valor)  # Excluye dígitos, punto y guion
        caracteres_raros_2010.extend(encontrados)

# Contar ocurrencias totales
conteo_caracteres_2010 = Counter(caracteres_raros_2010)

# Mostrar resultados
#print("Caracteres no numéricos encontrados en todo el DataFrame:", list(conteo_caracteres_2010.keys()))
#print("Frecuencias:", conteo_caracteres_2010)

# ----- Analizar carecteres raros dentro de la base de datos 2005 ------- #

# Selecciona las columnas numericas a partir de la columna 7 para hacer el analisis
sub_df_2005 = df_mun_tot_2005.iloc[:, 9:].astype(str)

# Inicializa una lista para almacenar caracteres raros
caracteres_raros_2005 = []

# Recorre cada columna y cada valor
for col in sub_df_2005.columns:
    for valor in sub_df_2005[col]:
        encontrados = re.findall(r'[^0-9\.\-]', valor)  # Excluye dígitos, punto y guion
        caracteres_raros_2005.extend(encontrados)

# Contar ocurrencias totales
conteo_caracteres_2005 = Counter(caracteres_raros_2005)

# Mostrar resultados
#print("Caracteres no numéricos encontrados en todo el DataFrame:", list(conteo_caracteres_2005.keys()))
#print("Frecuencias:", conteo_caracteres_2005)


# ----- Limpieza de datos 2020 ------- #

# Lista para coordenadas sospechosas
coordenadas_con_caracteres = []

def limpiar_columna(col):
    col_str = col.astype(str).str.strip()
    
    # Casos que deben ser convertidos a '0'
    solo_raros = col_str.isin(list(conteo_caracteres.keys())) | col.isna()
    
    # Casos con mezcla (no limpiar, solo registrar)
    contiene_raros = col_str.str.contains(r'[^0-9\.\-]', regex=True) & ~solo_raros

    # Reemplazo directo
    col_str[solo_raros] = '0'
    
    # Registro de coordenadas sospechosas
    coordenadas_con_caracteres.extend(zip(contiene_raros[contiene_raros].index, [col.name]*contiene_raros.sum()))
    
    return pd.to_numeric(col_str, errors='coerce')

# Aplicar a todas las columnas relevantes
sub_df = sub_df.apply(limpiar_columna)
sub_df = sub_df.apply(pd.to_numeric, errors='coerce')

# Actualizar el DataFrame original
df_mun_tot.iloc[:, 9:] = sub_df

# Mostrar coordenadas de valores sospechosos
df_coords = pd.DataFrame(coordenadas_con_caracteres, columns=['Fila', 'Columna'])
#df_coords

# ----- Limpieza de datos 2010 ------- #

# Lista para coordenadas sospechosas
coordenadas_con_caracteres_2010 = []

def limpiar_columna(col):
    col_str = col.astype(str).str.strip()
    
    # Casos que deben ser convertidos a '0'
    solo_raros = col_str.isin(list(conteo_caracteres_2010.keys())) | col.isna()
    
    # Casos con mezcla (no limpiar, solo registrar)
    contiene_raros = col_str.str.contains(r'[^0-9\.\-]', regex=True) & ~solo_raros

    # Reemplazo directo
    col_str[solo_raros] = '0'
    
    # Registro de coordenadas sospechosas
    coordenadas_con_caracteres_2010.extend(zip(contiene_raros[contiene_raros].index, [col.name]*contiene_raros.sum()))
    
    return pd.to_numeric(col_str, errors='coerce')

# Aplicar a todas las columnas relevantes
sub_df_2010 = sub_df_2010.apply(limpiar_columna)
sub_df_2010 = sub_df_2010.apply(pd.to_numeric, errors='coerce')

# Actualizar el DataFrame original
df_mun_tot_2010.iloc[:, 9:] = sub_df_2010

# Mostrar coordenadas de valores sospechosos
df_coords_2010 = pd.DataFrame(coordenadas_con_caracteres_2010, columns=['Fila', 'Columna'])
#filas_objetivo = [3810, 4179, 4180]
#f_mun_tot_2010.loc[filas_objetivo, 'tam_loc'] = df_mun_tot_2010.loc[filas_objetivo, 'tam_loc'].fillna(0)

# ----- Limpieza de datos 2005 ------- #

# Lista para coordenadas sospechosas
coordenadas_con_caracteres_2005 = []

def limpiar_columna(col):
    col_str = col.astype(str).str.strip()
    
    # Casos que deben ser convertidos a '0'
    solo_raros = col_str.isin(list(conteo_caracteres_2005.keys())) | col.isna()
    
    # Casos con mezcla (no limpiar, solo registrar)
    contiene_raros = col_str.str.contains(r'[^0-9\.\-]', regex=True) & ~solo_raros

    # Reemplazo directo
    col_str[solo_raros] = '0'
    
    # Registro de coordenadas sospechosas
    coordenadas_con_caracteres_2005.extend(zip(contiene_raros[contiene_raros].index, [col.name]*contiene_raros.sum()))
    
    return pd.to_numeric(col_str, errors='coerce')

# Aplicar a todas las columnas relevantes
sub_df_2005 = sub_df_2005.apply(limpiar_columna)
sub_df_2005 = sub_df_2005.apply(pd.to_numeric, errors='coerce')

# Actualizar el DataFrame original
df_mun_tot_2005.iloc[:, 9:] = sub_df_2005

# Mostrar coordenadas de valores sospechosos
#df_coords = pd.DataFrame(coordenadas_con_caracteres_2005, columns=['Fila', 'Columna'])
#df_coords


# ------ Corroboramos que este bien 2020 ------- #

sub_df = df_mun_tot.iloc[:, 9:].copy()
# Inicializa una lista para almacenar caracteres raros
caracteres_raros = []

# Recorre cada columna y cada valor
for col in sub_df.columns:
    for valor in sub_df[col]:
        encontrados = re.findall(r'[^0-9\.\-]', str(valor))  # Excluye dígitos, punto y guion
        caracteres_raros.extend(encontrados)

# Contar ocurrencias totales
conteo_caracteres = Counter(caracteres_raros)

# Mostrar resultados
#print("Caracteres no numéricos encontrados en todo el DataFrame:", list(conteo_caracteres.keys()))
#print("Frecuencias:", conteo_caracteres)


# ------ Convertir coordenadas DMS a decimal ------- #
df_mun_tot = df_mun_tot.drop(columns=['ALTITUD'], errors='ignore')

df_mun_tot['LAT_DECIMAL'] = df_mun_tot['LATITUD'].apply(dms_a_decimal)
df_mun_tot['LON_DECIMAL'] = df_mun_tot['LONGITUD'].apply(dms_a_decimal)

# Obtener las posiciones originales de LATITUD y LONGITUD
pos_lat = df_mun_tot.columns.get_loc('LATITUD')
pos_lon = df_mun_tot.columns.get_loc('LONGITUD')

# Insertar columnas nuevas en las mismas posiciones
df_mun_tot.insert(pos_lat, 'LAT_DECIMAL', df_mun_tot.pop('LAT_DECIMAL'))
df_mun_tot.insert(pos_lon, 'LON_DECIMAL', df_mun_tot.pop('LON_DECIMAL'))

# Eliminar columnas originales
df_mun_tot = df_mun_tot.drop(columns=['LATITUD', 'LONGITUD'])

# ------ Corroboramos que este bien 2010 ------- #

sub_df = df_mun_tot_2010.iloc[:, 9:].copy()
# Inicializa una lista para almacenar caracteres raros
caracteres_raros = []

# Recorre cada columna y cada valor
for col in sub_df.columns:
    for valor in sub_df[col]:
        encontrados = re.findall(r'[^0-9\.\-]', str(valor))  # Excluye dígitos, punto y guion
        caracteres_raros.extend(encontrados)

# Contar ocurrencias totales
conteo_caracteres = Counter(caracteres_raros)

# Mostrar resultados
#print("Caracteres no numéricos encontrados en todo el DataFrame:", list(conteo_caracteres.keys()))
#print("Frecuencias:", conteo_caracteres)

# ------ Corroboramos que este bien 2005 ------- #

sub_df = df_mun_tot_2005.iloc[:, 9:].copy()
# Inicializa una lista para almacenar caracteres raros
caracteres_raros_2005 = []

# Recorre cada columna y cada valor
for col in sub_df.columns:
    for valor in sub_df[col]:
        encontrados = re.findall(r'[^0-9\.\-]', str(valor))  # Excluye dígitos, punto y guion
        caracteres_raros_2005.extend(encontrados)

# Contar ocurrencias totales
conteo_caracteres_2005 = Counter(caracteres_raros_2005)

# Mostrar resultados
#print("Caracteres no numéricos encontrados en todo el DataFrame:", list(conteo_caracteres_2005.keys()))
#print("Frecuencias:", conteo_caracteres_2005)

### Datos Poblacionales

In [ ]:

df_poblacion = construir_df(
    df_2020=df_mun_tot,
    df_2010=df_mun_tot_2010,
    df_2005=df_mun_tot_2005,
    df_2000=df_2000,
    df_1995=df_1995,
    df_1990=df_1990,
    col_2020='POBTOT',
    col_2010='pobtot',
    col_2005='p_total',
    col_2000='pobtot',
    col_1995='POBTOTAL\t',
    col_1990='P_TOTAL\t',
    estado='Sinaloa',
    municipio='Mazatlán'
)

lista_sinaloa = df_poblacion['Población Sinaloa'].tolist()
lista_mazatlan = df_poblacion['Población Mazatlán'].tolist()
lista_villa_union = df_poblacion['Población Villa Unión'].tolist()

# Años base y población
años = np.array([1990, 1995, 2000, 2005, 2010, 2020])
t = años - 1990  # convertir a t = 0 para 1990

# Poblaciones
pob_sinaloa = np.array(lista_sinaloa)
pob_mazatlan = np.array(lista_mazatlan)
pob_villa_union = np.array(lista_villa_union)

# Función para ajustar modelo exponencial y predecir
def proyectar_poblacion(t, poblacion, años_futuros, base_year=1990):
    log_pob = np.log(poblacion)
    coef = np.polyfit(t, log_pob, 1)
    a, b = coef[1], coef[0]
    #print(f"Modelo: ln(P) = {a:.4f} + {b:.4f} * t")
    
    t_futuro = np.array(años_futuros) - base_year
    pob_futura = np.exp(a + b * t_futuro)
    return pob_futura

# Años a proyectar
años_futuros = [2025, 2030, 2035]

# Proyecciones
proj_sinaloa = proyectar_poblacion(t, pob_sinaloa, años_futuros)
proj_mazatlan = proyectar_poblacion(t, pob_mazatlan, años_futuros)
proj_vu = proyectar_poblacion(t, pob_villa_union, años_futuros)

# Crear DataFrame con resultados
df_proy = pd.DataFrame({
    'Año': años_futuros,
    'Sinaloa': np.round(proj_sinaloa).astype(int),
    'Mazatlán': np.round(proj_mazatlan).astype(int),
    'Villa Unión': np.round(proj_vu).astype(int)
})


# Renombrar columnas de df_proy para que coincidan con df_poblacion
df_proy_renombrado = df_proy.rename(columns={
    'Sinaloa': 'Población Sinaloa',
    'Mazatlán': 'Población Mazatlán',
    'Villa Unión': 'Población Villa Unión'
})

# Unir los dos DataFrames
df_poblacion_completa = pd.concat([df_poblacion, df_proy_renombrado], ignore_index=True)

# Calcular incrementos porcentuales
df_poblacion_completa['% Crecimiento Sinaloa'] = df_poblacion_completa['Población Sinaloa'].pct_change().fillna(0) * 100
df_poblacion_completa['% Crecimiento Mazatlán'] = df_poblacion_completa['Población Mazatlán'].pct_change().fillna(0) * 100
df_poblacion_completa['% Crecimiento Villa Unión'] = df_poblacion_completa['Población Villa Unión'].pct_change().fillna(0) * 100

# Redondear los resultados
df_poblacion_completa[['% Crecimiento Sinaloa', '% Crecimiento Mazatlán', '% Crecimiento Villa Unión']] = (df_poblacion_completa[['% Crecimiento Sinaloa', '% Crecimiento Mazatlán', '% Crecimiento Villa Unión']].round(2))

df_poblacion_completa

In [ ]:
# --- Gráfico 2: Evolución normalizada ---
# Normalizar al valor inicial de 1990 (primer fila)
df_normalizado = df_poblacion_completa.copy()
df_normalizado['Sinaloa %'] = df_normalizado['Población Sinaloa'] / df_normalizado['Población Sinaloa'].iloc[0] * 100
df_normalizado['Mazatlán %'] = df_normalizado['Población Mazatlán'] / df_normalizado['Población Mazatlán'].iloc[0] * 100
df_normalizado['Villa Unión %'] = df_normalizado['Población Villa Unión'] / df_normalizado['Población Villa Unión'].iloc[0] * 100

# Graficar
plt.figure(figsize=(10, 6))
plt.plot(df_normalizado['Año'], df_normalizado['Sinaloa %'], label='Sinaloa', marker='o')
plt.plot(df_normalizado['Año'], df_normalizado['Mazatlán %'], label='Mazatlán', marker='o')
plt.plot(df_normalizado['Año'], df_normalizado['Villa Unión %'], label='Villa Unión', marker='o')

plt.title('Crecimiento relativo de la población (1990 = 100%)')
plt.xlabel('Año')
plt.ylabel('Índice de crecimiento (%)')
plt.grid(True, linestyle='--', linewidth=0.5)
plt.legend()
plt.tight_layout()
plt.show()


Crecimiento relativo (normalizado a 1990 = 100%): muestra el crecimiento proporcional de cada localidad. Aunque Villa Unión tiene una población menor, ha crecido más aceleradamente en términos porcentuales.

### Densidad poblacional por vivienda

In [ ]:
# Datos de la población 2020
den_pob_sin = df_mun_tot[df_mun_tot['NOM_ENT'] == estado ]['PROM_OCUP'].iloc[0]
den_pob_maza = df_mun_tot[(df_mun_tot['NOM_MUN'] == municipio) & (df_mun_tot['NOM_LOC'] == municipio)]['PROM_OCUP'].iloc[0]
den_pob_villa_u = df_mun_tot[(df_mun_tot['NOM_MUN'] == municipio) & (df_mun_tot['NOM_LOC'] == 'Villa Unión')]['PROM_OCUP'].iloc[0]

# datos 2010
den_pob_sin_2010 = df_mun_tot_2010[df_mun_tot_2010['nom_ent'] == estado ]['prom_ocup'].iloc[0]
den_pob_maza_2010 = df_mun_tot_2010[(df_mun_tot_2010['nom_mun'] == municipio) & (df_mun_tot_2010['nom_loc'] == municipio)]['prom_ocup'].iloc[0]
den_pob_villa_u_2010 = df_mun_tot_2010[(df_mun_tot_2010['nom_mun'] == municipio) & (df_mun_tot_2010['nom_loc'] == 'Villa Unión')]['prom_ocup'].iloc[0]

# datos 2005
den_pob_sin_2005 = df_mun_tot_2005[df_mun_tot_2005['nom_ent'] == estado ]['pro_vipa'].iloc[0]
den_pob_maza_2005 = df_mun_tot_2005[(df_mun_tot_2005['nom_mun'] == municipio) & (df_mun_tot_2005['nom_loc'] == municipio)]['pro_vipa'].iloc[0]
den_pob_villa_u_2005 = df_mun_tot_2005[(df_mun_tot_2005['nom_mun'] == municipio) & (df_mun_tot_2005['nom_loc'] == 'Villa Unión')]['pro_vipa'].iloc[0]

# datos 2000
den_pob_sin_2000 = df_2000[df_2000['nom_ent'] == estado ]['pro_ovp'].iloc[0]
den_pob_maza_2000 = df_2000[(df_2000['nom_mun'] == municipio) & (df_2000['nom_loc'] == 'MAZATLAN')]['pro_ovp'].iloc[0]
den_pob_villa_u_2000 = df_2000[(df_2000['nom_mun'] == municipio) & (df_2000['nom_loc'] == 'VILLA UNION')]['pro_ovp'].iloc[0]

# Datos de la población 1995
den_pob_sin_1995 = df_1995[df_1995['NOM_ENT\t'] == estado ]['PRO_O_VP\t'].iloc[0]
den_pob_maza_1995 = df_1995[(df_1995['NOM_MUN\t'] == municipio) & (df_1995['NOM_LOC\t'] == 'MAZATLAN')]['PRO_O_VP\t'].iloc[0]
den_pob_villa_u_1995 = df_1995[(df_1995['NOM_MUN\t'] == municipio) & (df_1995['NOM_LOC\t'] == 'VILLA UNION')]['PRO_O_VP\t'].iloc[0]

# Datos de la población 1990
den_pob_sin_1990 = df_1990[df_1990['NOM_ENT\t'] == estado ]['PROM_VIV\t'].iloc[0]
den_pob_maza_1990 = df_1990[(df_1990['NOM_MUN\t'] == municipio) & (df_1990['NOM_LOC\t'] == 'MAZATLAN')]['PROM_VIV\t'].iloc[0]
den_pob_villa_u_1990 = df_1990[(df_1990['NOM_MUN\t'] == municipio) & (df_1990['NOM_LOC\t'] == 'VILLA UNION')]['PROM_VIV\t'].iloc[0]



# Crear el DataFrame con los datos recolectados
df_den_poblacion = pd.DataFrame({
    'Año': [1990, 1995,2000, 2005, 2010, 2020],
    'Personas x vivienda en Sinaloa': [den_pob_sin_1990, den_pob_sin_1995, den_pob_sin_2000, den_pob_sin_2005, den_pob_sin_2010, den_pob_sin],
    'Personas x vivienda en Mazatlán': [den_pob_maza_1990, den_pob_maza_1995, den_pob_maza_2000, den_pob_maza_2005, den_pob_maza_2010, den_pob_maza],
    'Personas x vivienda en Villa Unión': [den_pob_villa_u_1990, den_pob_villa_u_1995, den_pob_villa_u_2000, den_pob_villa_u_2005, den_pob_villa_u_2010, den_pob_villa_u]
})

# Años base y población
años = np.array([1990, 1995, 2000, 2005, 2010, 2020])
t = años - 1990  # convertir a t = 0 para 1990

# Densidad de población
den_pob_sinaloa = np.array([den_pob_sin_1990, den_pob_sin_1995, den_pob_sin_2000, den_pob_sin_2005, den_pob_sin_2010, den_pob_sin])
den_pob_mazatlan = np.array([den_pob_maza_1990, den_pob_maza_1995, den_pob_maza_2000, den_pob_maza_2005, den_pob_maza_2010, den_pob_maza])
den_pob_villa_union = np.array([den_pob_villa_u_1990, den_pob_villa_u_1995, den_pob_villa_u_2000, den_pob_villa_u_2005, den_pob_villa_u_2010, den_pob_villa_u])

# Función para ajustar modelo exponencial y predecir
def proyectar_poblacion(t, poblacion, años_futuros, base_year=1990):
    poblacion = np.array(poblacion, dtype=float)
    log_pob = np.log(poblacion)
    coef = np.polyfit(t, log_pob, 1)
    a, b = coef[1], coef[0]
    #print(f"Modelo: ln(P) = {a:.4f} + {b:.4f} * t")
    
    t_futuro = np.array(años_futuros) - base_year
    pob_futura = np.exp(a + b * t_futuro)
    return pob_futura

# Años a proyectar
años_futuros = [2025, 2030, 2035]

# Proyecciones
proj_sinaloa = proyectar_poblacion(t, den_pob_sinaloa, años_futuros)

proj_vu = proyectar_poblacion(t, den_pob_villa_union, años_futuros)

# Crear DataFrame con resultados
df_proy = pd.DataFrame({
    'Año': años_futuros,
    'Sinaloa': proj_sinaloa.round(2),
    'Mazatlán': proj_mazatlan.round(2),
    'Villa Unión': proj_vu.round(2)
})
# Renombrar columnas de df_proy para que coincidan con df_poblacion
df_proy_renombrado = df_proy.rename(columns={
    'Sinaloa': 'Personas x vivienda en Sinaloa',
    'Mazatlán': 'Personas x vivienda en Mazatlán',
    'Villa Unión': 'Personas x vivienda en Villa Unión'
})

# Unir los dos DataFrames
df_den_poblacion_completa = pd.concat([df_den_poblacion, df_proy_renombrado], ignore_index=True)
df_den_poblacion_completa

### Población economicamente activa

In [ ]:

# datos 2020
den_pob_maza = df_mun_tot[(df_mun_tot['NOM_MUN'] == municipio) & (df_mun_tot['NOM_LOC'] == municipio)]['PEA'].iloc[0]
den_pob_villa_u = df_mun_tot[(df_mun_tot['NOM_MUN'] == municipio) & (df_mun_tot['NOM_LOC'] == 'Villa Unión')]['PEA'].iloc[0]

# datos 2010
den_pob_maza_2010 = df_mun_tot_2010[(df_mun_tot_2010['nom_mun'] == municipio) & (df_mun_tot_2010['nom_loc'] == municipio)]['pea'].iloc[0]
den_pob_villa_u_2010 = df_mun_tot_2010[(df_mun_tot_2010['nom_mun'] == municipio) & (df_mun_tot_2010['nom_loc'] == 'Villa Unión')]['pea'].iloc[0]


# datos 2000
den_pob_maza_2000 = df_2000[(df_2000['nom_mun'] == municipio) & (df_2000['nom_loc'] == 'MAZATLAN')]['pecoactiv'].iloc[0]
den_pob_villa_u_2000 = df_2000[(df_2000['nom_mun'] == municipio) & (df_2000['nom_loc'] == 'VILLA UNION')]['pecoactiv'].iloc[0]


# Datos de la población 1990
den_pob_maza_1990 = df_1990[(df_1990['NOM_MUN\t'] == municipio) & (df_1990['NOM_LOC\t'] == 'MAZATLAN')]['P_E_ACT\t'].iloc[0]
den_pob_villa_u_1990 = df_1990[(df_1990['NOM_MUN\t'] == municipio) & (df_1990['NOM_LOC\t'] == 'VILLA UNION')]['P_E_ACT\t'].iloc[0]


# Crear el DataFrame con los datos recolectados
df_den_poblacion = pd.DataFrame({
    'Año': [1990,2000, 2010, 2020],
    'Personas economicamente activas Mazatlán': [den_pob_maza_1990, den_pob_maza_2000, den_pob_maza_2010, den_pob_maza],
    'Personas economicamente activas Villa Unión': [den_pob_villa_u_1990, den_pob_villa_u_2000, den_pob_villa_u_2010, den_pob_villa_u]
})

# Años base y población
años = np.array([1990, 2000, 2010, 2020])
t = años - 1990  # convertir a t = 0 para 1990

# Densidad de población
den_pob_mazatlan = np.array([den_pob_maza_1990, den_pob_maza_2000, den_pob_maza_2010, den_pob_maza])
den_pob_villa_union = np.array([den_pob_villa_u_1990, den_pob_villa_u_2000, den_pob_villa_u_2010, den_pob_villa_u])

# Función para ajustar modelo exponencial y predecir
def proyectar_poblacion(t, poblacion, años_futuros, base_year=1990):
    poblacion = np.array(poblacion, dtype=float)
    log_pob = np.log(poblacion)
    coef = np.polyfit(t, log_pob, 1)
    a, b = coef[1], coef[0]
    #print(f"Modelo: ln(P) = {a:.4f} + {b:.4f} * t")
    
    t_futuro = np.array(años_futuros) - base_year
    pob_futura = np.exp(a + b * t_futuro)
    return pob_futura

# Años a proyectar
años_futuros = [2030, 2040, 2050]

# Proyecciones
proj_mazatlan = proyectar_poblacion(t, den_pob_mazatlan, años_futuros)
proj_vu = proyectar_poblacion(t, den_pob_villa_union, años_futuros)

# Crear DataFrame con resultados
df_proy = pd.DataFrame({
    'Año': años_futuros,
    'Personas economicamente activas Mazatlán': proj_mazatlan.round(2),
    'Personas economicamente activas Villa Unión': proj_vu.round(2)
})
df_proy




# Unir los dos DataFrames
df_den_poblacion_completa = pd.concat([df_den_poblacion, df_proy], ignore_index=True)
df_den_poblacion_completa

### Vivindas

In [ ]:
# Datos de la población 2020
viv_sin = df_mun_tot[df_mun_tot['NOM_ENT'] == estado ]['VIVTOT'].iloc[0]
viv_maza = df_mun_tot[(df_mun_tot['NOM_MUN'] == municipio) & (df_mun_tot['NOM_LOC'] == municipio)]['VIVTOT'].iloc[0]
viv_villa_u = df_mun_tot[(df_mun_tot['NOM_MUN'] == municipio) & (df_mun_tot['NOM_LOC'] == 'Villa Unión')]['VIVTOT'].iloc[0]

# datos 2010
viv_sin_2010 = df_mun_tot_2010[df_mun_tot_2010['nom_ent'] == estado ]['vivtot'].iloc[0]
viv_maza_2010 = df_mun_tot_2010[(df_mun_tot_2010['nom_mun'] == municipio) & (df_mun_tot_2010['nom_loc'] == municipio)]['vivtot'].iloc[0]
viv_villa_u_2010 = df_mun_tot_2010[(df_mun_tot_2010['nom_mun'] == municipio) & (df_mun_tot_2010['nom_loc'] == 'Villa Unión')]['vivtot'].iloc[0]

# datos 2005
viv_sin_2005 = df_mun_tot_2005[df_mun_tot_2005['nom_ent'] == estado ]['t_vivhab'].iloc[0]
viv_maza_2005 = df_mun_tot_2005[(df_mun_tot_2005['nom_mun'] == municipio) & (df_mun_tot_2005['nom_loc'] == municipio)]['t_vivhab'].iloc[0]
viv_villa_u_2005 = df_mun_tot_2005[(df_mun_tot_2005['nom_mun'] == municipio) & (df_mun_tot_2005['nom_loc'] == 'Villa Unión')]['t_vivhab'].iloc[0]

# datos 2000
viv_sin_2000 = df_2000[df_2000['nom_ent'] == estado ]['totvivhab'].iloc[0]
viv_maza_2000 = df_2000[(df_2000['nom_mun'] == municipio) & (df_2000['nom_loc'] == 'MAZATLAN')]['totvivhab'].iloc[0]
viv_villa_u_2000 = df_2000[(df_2000['nom_mun'] == municipio) & (df_2000['nom_loc'] == 'VILLA UNION')]['totvivhab'].iloc[0]

# Datos de la población 1995
viv_sin_1995 = df_1995[df_1995['NOM_ENT\t'] == estado ]['TOTVIVH\t'].iloc[0]
viv_maza_1995 = df_1995[(df_1995['NOM_MUN\t'] == municipio) & (df_1995['NOM_LOC\t'] == 'MAZATLAN')]['TOTVIVH\t'].iloc[0]
viv_villa_u_1995 = df_1995[(df_1995['NOM_MUN\t'] == municipio) & (df_1995['NOM_LOC\t'] == 'VILLA UNION')]['TOTVIVH\t'].iloc[0]

# Datos de la población 1990
viv_sin_1990 = df_1990[df_1990['NOM_ENT\t'] == estado ]['T_VIVHAB\t'].iloc[0]
viv_maza_1990 = df_1990[(df_1990['NOM_MUN\t'] == municipio) & (df_1990['NOM_LOC\t'] == 'MAZATLAN')]['T_VIVHAB\t'].iloc[0]
viv_villa_u_1990 = df_1990[(df_1990['NOM_MUN\t'] == municipio) & (df_1990['NOM_LOC\t'] == 'VILLA UNION')]['T_VIVHAB\t'].iloc[0]



# Crear el DataFrame con los datos recolectados
df_viv = pd.DataFrame({
    'Año': [1990, 1995,2000, 2005, 2010, 2020],
    'Vivienda en Sinaloa': [viv_sin_1990, viv_sin_1995, viv_sin_2000, viv_sin_2005, viv_sin_2010, viv_sin],
    'Vivienda en Mazatlán': [viv_maza_1990, viv_maza_1995, viv_maza_2000, viv_maza_2005, viv_maza_2010, viv_maza],
    'Vivienda en Villa Unión': [viv_villa_u_1990, viv_villa_u_1995, viv_villa_u_2000, viv_villa_u_2005, viv_villa_u_2010, viv_villa_u]
})
# Viviendas
viv_sinaloa = np.array([viv_sin_1990, viv_sin_1995, viv_sin_2000, viv_sin_2005, viv_sin_2010, viv_sin])
viv_mazatlan = np.array([viv_maza_1990, viv_maza_1995, viv_maza_2000, viv_maza_2005, viv_maza_2010, viv_maza])
viv_villa_union = np.array([viv_villa_u_1990, viv_villa_u_1995, viv_villa_u_2000, viv_villa_u_2005, viv_villa_u_2010, viv_villa_u])
# Años base y población
años = np.array([1990, 1995, 2000, 2005, 2010, 2020])
t = años - 1990  # convertir a t = 0 para 1990
# Función para ajustar modelo exponencial y predecir
def proyectar_poblacion(t, poblacion, años_futuros, base_year=1990):
    poblacion = np.array(poblacion, dtype=float)
    log_pob = np.log(poblacion)
    coef = np.polyfit(t, log_pob, 1)
    a, b = coef[1], coef[0]
    #print(f"Modelo: ln(P) = {a:.4f} + {b:.4f} * t")
    
    t_futuro = np.array(años_futuros) - base_year
    pob_futura = np.exp(a + b * t_futuro)
    return pob_futura

# Años a proyectar
años_futuros = [2025, 2030, 2035]

# Proyecciones
proj_sinaloa = proyectar_poblacion(t, viv_sinaloa, años_futuros)
proj_mazatlan = proyectar_poblacion(t, viv_mazatlan, años_futuros)
proj_vu = proyectar_poblacion(t, viv_villa_union, años_futuros)

# Crear DataFrame con resultados
df_proy = pd.DataFrame({
    'Año': años_futuros,
    'Sinaloa': proj_sinaloa.round(0),
    'Mazatlán': proj_mazatlan.round(0),
    'Villa Unión': proj_vu.round(0)
})
# Renombrar columnas de df_proy para que coincidan con df_poblacion
df_proy_renombrado = df_proy.rename(columns={
    'Sinaloa': 'Vivienda en Sinaloa',
    'Mazatlán': 'Vivienda en Mazatlán',
    'Villa Unión': 'Vivienda en Villa Unión'
})

# Unir los dos DataFrames
df_viv_completa = pd.concat([df_viv, df_proy_renombrado], ignore_index=True)
df_viv_completa

### Viviendas sin servicios basicos

**1. Detección de localidades con mayor déficit de servicios básicos**

Se identifican las localidades con mayor carencia en servicios elementales mediante el análisis de las siguientes columnas:

- **`VPH_S_ELEC`**: Viviendas particulares habitadas **sin energía eléctrica**  
- **`VPH_AGUAFV`**: Viviendas particulares habitadas **sin agua entubada** dentro de la vivienda  
- **`VPH_NODREN`**: Viviendas particulares habitadas **sin drenaje**  
- **`VPH_NDEAED`**: Viviendas particulares habitadas **sin energía eléctrica, agua entubada ni drenaje**
**🔍 Insight potencial:**

Las localidades con una **alta proporción de viviendas sin acceso a servicios básicos** representan zonas prioritarias para el desarrollo de **proyectos de vivienda social o progresiva**.


In [ ]:
lista_valores_eliminar_2020 = ['Ninguno','Total del Municipio','Total AGEB urbana', 'Total de la localidad urbana', 'Total del municipio','Localidades de una vivienda','Localidades de dos viviendas']

df_mun_tot = df_mun_tot[df_mun_tot['NOM_MUN'] == municipio].copy()
df_filtrado_2020 = df_mun_tot[~df_mun_tot['NOM_LOC'].isin(lista_valores_eliminar_2020)]
df_filtrado_2020 = df_filtrado_2020.iloc[:, 5:].copy()
df_filtrado_2020 = df_filtrado_2020.sort_values(by='POBTOT', ascending=False)


# Coordenadas de Villa Unión (desde el DataFrame original que sí tiene coordenadas)
coord_villa_union = (
    df_mun_tot[df_mun_tot['NOM_LOC'] == 'Villa Unión']['LAT_DECIMAL'].values[0],
    df_mun_tot[df_mun_tot['NOM_LOC'] == 'Villa Unión']['LON_DECIMAL'].values[0]
)

# Copiar solo lo necesario
df_deficit_serv = df_filtrado_2020[["NOM_LOC",'LON_DECIMAL','LAT_DECIMAL', "VIVTOT", "VPH_S_ELEC", "VPH_AGUAFV", "VPH_NODREN",'VPH_NDEAED']].copy()

# Calcular porcentaje promedio de viviendas sin servicios básicos
df_deficit_serv["% sin servicios electricidad"] = (df_deficit_serv["VPH_S_ELEC"] / df_deficit_serv["VIVTOT"]) * 100
df_deficit_serv["% sin servicios agua"] = (df_deficit_serv["VPH_AGUAFV"] / df_deficit_serv["VIVTOT"]) *100
df_deficit_serv["% sin servicios drenaje"] = (df_deficit_serv["VPH_NODREN"] / df_deficit_serv["VIVTOT"]) *100
df_deficit_serv["% sin ningun servicios"] = (df_deficit_serv["VPH_NDEAED"] / df_deficit_serv["VIVTOT"])*100
df_deficit_serv["% sin servicios totales"] = (df_deficit_serv["% sin servicios electricidad"] + df_deficit_serv["% sin servicios agua"] + df_deficit_serv["% sin servicios drenaje"] + df_deficit_serv["% sin ningun servicios"]) / 4

# ------ Basado en el % de viviendas sin servicios calculamos las viviendas necesarios de calidad de vida ------ #

df_deficit_serv["Viviendas dignas necesarias"] =  (
    df_deficit_serv["VPH_S_ELEC"] +
    df_deficit_serv["VPH_AGUAFV"] +
    df_deficit_serv["VPH_NODREN"] + 
    df_deficit_serv["VPH_NDEAED"]
    )


df_deficit_serv['Distancia a Villa Unión (km)'] = df_deficit_serv.apply(
    lambda row: geodesic(coord_villa_union, (row['LAT_DECIMAL'], row['LON_DECIMAL'])).km,
    axis=1
)

# Filtrar localidades distintas a Villa Unión
#df_filtrado = df_deficit_serv[df_deficit_serv['NOM_LOC'] != 'Villa Unión']

# Filtrar localidades a 25 km o menos de Villa Unión
df_cercanas_deficit = df_deficit_serv[df_deficit_serv['Distancia a Villa Unión (km)'] <= 25] \
    .sort_values(by='% sin servicios totales',ascending=False)


df_cercanas_deficit = df_cercanas_deficit[df_cercanas_deficit["% sin servicios totales"] > 0].copy()
df_cercanas_deficit = df_cercanas_deficit.sort_values(by='Viviendas dignas necesarias', ascending=False)
total_viv_nec = df_cercanas_deficit["Viviendas dignas necesarias"].sum()
print(f"Total de viviendas dignas necesarias en localidades cercanas a Villa Unión y Villa Unión: {total_viv_nec}")
df_cercanas_deficit.to_csv('Localidades- Viviendas dignas- Cerca de Villa Union.csv', index=False, encoding='ISO-8859-1')

df_cercanas_deficit.head(3)

### Analisis Denues

In [19]:
# Ruta relativa al archivo CSV con los datos de DENUE
denue = leer_archivo("C:/Users/julio/OneDrive/Documentos/Trabajo/IdeasFrscas/Proyecto Villa Union/Base de datos/INEGI_DENUE_20052025.csv") 

# Diccionario scian
scian = leer_archivo("C:/Users/julio/OneDrive/Documentos/Trabajo/IdeasFrscas/Bases de datos/Diccionario SCIAN.xlsx") 

# Diccionario de datos de la base de datos SCIAN, 
scian = scian[scian["Código"].astype(str).str.fullmatch(r"^\d{3}")] # Se filtro solo a los codigos de 3 digitos que nos indican la principal actividad economico
scian["Título"] = scian["Título"] .str.rstrip("T") # Se limpia los datos de la Columna Título
scian = scian[["Código", "Título"]] # Solo usas las siguentes columnas para hacer el filtro 

# Diccionario de Variables 
'''
Diccionario de Columnas a Utilizar 
Nombre de la Unidad Económica: Es el nombre comercial o nombre exterior con el que se identifica o anuncia la unidad económica.

Código de la clase de actividad SCIAN: El código está asignado con base en la actividad principal que desarrolla la unidad económica y de acuerdo con el Sistema de Clasificación
Industrial para América del Norte.

Descripcion estrato personal ocupado: Permite identificar el tamaño de Unidades Económicas por el número
de personal que emplean.

Tipo de vialidad: Es la superficie del terreno destinada para el tránsito vehicular y/o peatonal, en la cual se encuentra ubicada la unidad económica (calle, avenida,
andado.

Tipo de asentamiento humano: Es la clasificación que se da al asentamiento humano de acuerdo con su función (colonia, fraccionamiento, unidad habitacional, etc.).

Nombre de asentamiento humano:Es el sustantivo propio con el cual se identifica el asentamiento humano.

Tipo centro comercial: Son los caracteres alfanuméricos con los que se identifica el tipo de plaza, centro comercial, mercado.

Tipo de establecimiento: En este tipo de establecimiento están comprendidas las viviendas cuando en algún espacio de la casa-habitación, que también está destinado a
otras actividades cotidianas, se realiza alguna actividad económica.

Fecha de incorporación al DENUE: Fecha en la que la unidad económica se integró al Directorio Estadístico Nacional de Unidades Económicas.

Área geoestadística básica: Marco Geoestadístico Naciona.

Manzana: xtensión territorial que está constituida por un grupo de
viviendas, edificios, predios, lotes o terrenos de uso habitacional, comercial, industrial o de servicios.

Latitud: Es la distancia que existe entre la unidad económica y el ecuador. 

Fecha en la que la unidad económica se integró al Directorio Estadístico Nacional de Unidades Económicas.

Longitud: Es la distancia que existe entre la unidad económica y el meridiano de Greenwich.-

'''

# Lista de variables a considerar y filtrado por esas columnas 
denues = denue[[
    'Nombre de la Unidad Económica',
    'Código de la clase de actividad SCIAN',
    'Descripcion estrato personal ocupado',
    'Tipo de vialidad',
    'Tipo de asentamiento humano',
    'Nombre de asentamiento humano',
    'Tipo centro comercial',
    'Corredor industrial, centro comercial o mercado público',
    'Fecha de incorporación al DENUE',
    'Área geoestadística básica ',
    'Manzana',
    'Latitud',
    'Longitud'
]].copy()


# ---- Limpieza de datos ----#

# Solo se considerará el año en la Fecha de incorporación al DENU
denues["Fecha de incorporación"] = denues['Fecha de incorporación al DENUE'].astype(str).str[:4]

# Posicionar la nueva columna en donde sea más facil leer la información 
col_f = denues.pop("Fecha de incorporación")
denues.insert(9,"Fecha de incorporación", col_f)


# ---- Principal actividad economica SCIAN de cada DENUE ----# 

# Considerar solo los tres primeros digitos  del SCIAN para hacer la conección con las dos bases de datos. 
denues["CLAVE SCIAN"] = denues["Código de la clase de actividad SCIAN"].astype(str).str[:3]

# Se unen las dos bases de datos para obtener la principal actividad economica
denue_c = denues.merge(scian,left_on="CLAVE SCIAN", right_on="Código", how = "left")

# Se renombra la columna a utilizar
denue_c = denue_c.rename(columns={"Título": "Principal Actividad Economica"})

# Se eliminan las columnas que ya no son necesarias 
denue_c = denue_c.drop(columns=["CLAVE SCIAN","Código","Fecha de incorporación al DENUE"])

# Posicionar la nueva columna en donde sea más facil leer la información 
col_a = denue_c.pop("Principal Actividad Economica")
denue_c.insert(2,"Principal Actividad Economica", col_a)

# Posicionar la nueva columna en donde sea más facil leer la información 
col_a = denue_c.pop("Principal Actividad Economica")
denue_c.insert(2,"Principal Actividad Economica", col_a)
# Diccionario de reemplazo amigable
reemplazos = {
    'Comercio al por menor de abarrotes, alimentos, bebidas, hielo y tabaco': 'Tiendas de abarrotes y comida',
    'Servicios de preparación de alimentos y bebidas': 'Restaurantes y comida',
    'Servicios de reparación y mantenimiento': 'Talleres y reparación',
    'Servicios personales': 'Servicios personales (peluquería, etc.)',
    'Comercio al por menor de productos textiles, bisutería, accesorios de vestir y calzado': 'Tiendas de ropa y calzado',
    'Industria alimentaria': 'Fábricas de alimentos',
    'Comercio al por menor de artículos de papelería, libros, revistas y periódicos': 'Papelerías',
    'Comercio al por menor de enseres domésticos, computadoras, artículos para la decoración de interiores y artículos usados': 'Tiendas de hogar',
    'Asociaciones y organizaciones': 'Organizaciones civiles',
    'Servicios médicos de consulta externa y servicios relacionados': 'Consultorios médicos',
    'Comercio al por mayor de materias primas agropecuarias y forestales, para la industria, y de desperdicios': 'Venta al mayoreo agrícola',
    'Comercio al por menor de vehículos de motor, refacciones, combustibles y lubricantes': 'Venta de autos y refacciones',
    'Comercio al por menor de artículos para el cuidado de la salud': 'Farmacias',
    'Servicios educativos': 'Escuelas',
    'Comercio al por menor de artículos de ferretería, tlapalería y vidrios': 'Ferreterías',
    'Instituciones de intermediación crediticia y financiera no bursátil': 'Bancos y financieras',
    'Comercio al por menor en tiendas de autoservicio': 'Supermercados',
    'Fabricación de productos metálicos': 'Fábricas de metal',
    'Servicios de entretenimiento en instalaciones recreativas y otros servicios recreativos': 'Centros de entretenimiento',
    'Otros servicios de asistencia social': 'Apoyo social',
    'Industria de la madera': 'Carpintería e industria de madera',
    'Actividades legislativas, gubernamentales y de impartición de justicia': 'Oficinas de gobierno',
    'Servicios de apoyo a los negocios': 'Servicios para negocios',
    'Servicios inmobiliarios': 'Inmobiliarias',
    'Servicios de alojamiento temporal': 'Hoteles',
    'Industria de las bebidas y del tabaco': 'Fábricas de bebidas',
    'Generación, transmisión, distribución y comercialización de energía eléctrica, agua y gas por ductos al consumidor final': 'Servicios de luz y energía',
    'Servicios profesionales, científicos y técnicos': 'Profesionistas (contadores, etc.)',
    'Servicios de alquiler de bienes muebles': 'Renta de equipo o muebles',
    'Comercio al por mayor de abarrotes, alimentos y bebidas': 'Venta mayorista de alimentos',
    'Comercio al por mayor de maquinaria, equipo y mobiliario para actividades agropecuarias, industriales y de servicios': 'Venta mayorista de maquinaria',
    'Telecomunicaciones': 'Servicios de telecomunicaciones',
    'Servicios relacionados con el transporte': 'Servicios de transporte',
    'Transporte terrestre de pasajeros, excepto por ferrocarril': 'Transporte público',
    'Fabricación de productos textiles, excepto prendas de vestir': 'Fábricas de textiles',
    'Fabricación de muebles, colchones y persianas': 'Fábricas de muebles',
    'Fabricación de prendas de vestir': 'Fábricas de ropa',
    'Pesca, caza y captura': 'Actividades pesqueras',
    'Fabricación de insumos textiles y acabado de textiles': 'Fábricas de telas',
    'Otras industrias manufactureras': 'Otras fábricas',
    'Curtido y acabado de cuero y piel, y fabricación de productos de cuero, piel y materiales sucedáneos': 'Fábricas de cuero',
    'Edificación': 'Empresas constructoras',
    'Transporte turístico': 'Transporte turístico',
    'Hospitales': 'Hospitales',
    'Residencias de asistencia social y para el cuidado de la salud': 'Casas de asistencia',
    'Manejo de residuos y servicios de remediación': 'Manejo de basura y reciclaje',
    'Museos, sitios históricos, zoológicos y similares': 'Museos y zoológicos'
}

# Reemplazar en el DataFrame
denue_c['Principal Actividad Economica'] = denue_c['Principal Actividad Economica'].replace(reemplazos)

# El 80% de las unidades economicas estan concentradas en las siguientes actividades economicas
concentrado_denue = analizar_columnas(denue_c,"Principal Actividad Economica",100)

# Crear el CSV de la base de datos filtrados 
concentrado_denue.to_csv("Pincipales actividades economicas Villa Union.csv", index=False, encoding='ISO-8859-1')

concentrado_denue


Estos son los datos que representan el 100% de los valores. De la columna Principal Actividad Economica


Principal Actividad Economica  Cantidad
0                       Tiendas de abarrotes y comida       206
1                               Restaurantes y comida       138
2                               Talleres y reparación       100
3             Servicios personales (peluquería, etc.)        54
4                           Tiendas de ropa y calzado        46
5                               Fábricas de alimentos        41
6   Comercio al por menor de artículos de papelerí...        36
7                                    Tiendas de hogar        36
8                              Organizaciones civiles        28
9                                Consultorios médicos        27
10  Comercio al por mayor de materias primas agrop...        26
11                       Venta de autos y refacciones        23
12                                          Farmacias        22
13                                           Escuelas        21
14                                        Ferreterías        19
15                               Bancos y financieras        17
16  Comercio al por menor en tiendas de autoservic...        16
17                                  Fábricas de metal        11
18                         Centros de entretenimiento        10
19                                       Apoyo social         8
20                  Carpintería e industria de madera         7
21                               Oficinas de gobierno         6
22                            Servicios para negocios         6
23                                      Inmobiliarias         5
24                                            Hoteles         4
25                                Fábricas de bebidas         4
26  Generación, transmisión, distribución y comerc...         4
27                  Profesionistas (contadores, etc.)         4
28                          Renta de equipo o muebles         4
29  Comercio al por mayor de abarrotes, alimentos,...         3
30  Comercio al por mayor de maquinaria, equipo y ...         3
31                    Servicios de telecomunicaciones         3
32                            Servicios de transporte         2
33                                 Transporte público         2
34                               Fábricas de textiles         2
35                                Fábricas de muebles         2
36                                   Fábricas de ropa         2
37                              Actividades pesqueras         1
38                                  Fábricas de telas         1
39                                     Otras fábricas         1
40                                  Fábricas de cuero         1
41                             Empresas constructoras         1
42                               Transporte turístico         1
43                                         Hospitales         1
44                                Casas de asistencia         1
45                       Manejo de basura y reciclaje         1
46                                Museos y zoológicos         1

In [20]:
import folium

mapa1 = folium.Map(location=[denue_c['Latitud'].mean(), denue_c['Longitud'].mean()], zoom_start=15)

for _, row in denue_c.iterrows():
    popup_text = f"<b>{row['Nombre de la Unidad Económica']}</b><br>Actividad: {row['Principal Actividad Economica']}"
    folium.Marker(
        location=[row['Latitud'], row['Longitud']],
        popup=popup_text,
        icon=folium.Icon(color="blue", icon="info-sign")
    ).add_to(mapa1)

mapa1.save("Mapa_Etiquetas_UNE_Actividad.html")
mapa1

In [ ]:
import qrcode
from PIL import Image, ImageDraw, ImageFont

# URL del mapa (debe reemplazarse por tu URL real si se sube a Drive o servidor)
url_mapa = "file:///C:/Users/julio/OneDrive/Documentos/Trabajo/IdeasFrscas/Proyecto%20Villa%20Union/Mapa_Etiquetas_UNE_Actividad.html"

# Generar código QR
qr = qrcode.make(url_mapa)
qr_path = "/mnt/data/qr_mapa_villa_union.png"
qr.save(qr_path)

In [16]:
from folium.plugins import HeatMap

mapa2 = folium.Map(location=[denue_c['Latitud'].mean(), denue_c['Longitud'].mean()], zoom_start=15)

# Preparar datos del heatmap
heat_data = denue_c[['Latitud', 'Longitud']].dropna().values.tolist()

HeatMap(heat_data, radius=12, blur=10, max_zoom=18).add_to(mapa2)

mapa2.save("Mapa_Calor_Comercios_VillaUnion.html")
mapa2

In [17]:
import seaborn as sns
from matplotlib.colors import to_hex  # Importar conversor de RGB a HEX

# Convertir a categoría
categorias = denue_c['Principal Actividad Economica'].astype('category')
denue_c['codigo_categoria'] = categorias.cat.codes

# Crear paleta de colores con número de categorías únicas
palette = sns.color_palette("tab20", len(categorias.cat.categories))

# Convertir la tupla RGB a hexadecimal
denue_c['color'] = denue_c['codigo_categoria'].apply(lambda x: to_hex(palette[x]))

import folium

mapa3 = folium.Map(location=[denue_c['Latitud'].mean(), denue_c['Longitud'].mean()], zoom_start=15)

for _, row in denue_c.iterrows():
    folium.CircleMarker(
        location=[row['Latitud'], row['Longitud']],
        radius=5,
        popup=f"<b>{row['Nombre de la Unidad Económica']}</b><br>{row['Principal Actividad Economica']}",
        color=row['color'],
        fill=True,
        fill_color=row['color'],
        fill_opacity=0.8
    ).add_to(mapa3)

mapa3.save("Mapa_Categorias_Economicas.html")

mapa3

In [18]:
# Crear un mapa centrado 
mapa = folium.Map(location=[denue_c['Latitud'].mean(), denue_c['Longitud'].mean()], zoom_start=16)

# Añadir los establecimientos al mapa
for index, row in denue_c.iterrows():
    folium.Marker([row['Latitud'], row['Longitud']], popup=row['Nombre de la Unidad Económica']).add_to(mapa)

# Guardar Mapa
mapa.save("Comercios Villa Unión por DENUE.html")
mapa

**Fecha de incorporación DENUE**

In [ ]:

# Calculamos el número de DENUES que tiene de 0 a 5 personas empleadas hasta los 251 y más
fecha_denue = denue_c['Fecha de incorporación'].value_counts().reset_index()

# Pasamos los reultados a un DataFrame
fecha_denue.columns = ["Fecha de incorporación", 'Cantidad']
# Ordenar por año (opcional pero recomendable para visualización)
fecha_denue = fecha_denue.sort_values(by="Fecha de incorporación")

# Definir t y población
t = fecha_denue["Fecha de incorporación"].astype(int).tolist()
denue_villa_anual = fecha_denue["Cantidad"].tolist()

# Función para proyectar
def proyectar_poblacion(t, poblacion, años_futuros, base_year=1990):
    poblacion = np.array(poblacion, dtype=float)
    log_pob = np.log(poblacion)
    coef = np.polyfit(np.array(t) - base_year, log_pob, 1)
    a, b = coef[1], coef[0]
    t_futuro = np.array(años_futuros) - base_year
    pob_futura = np.exp(a + b * t_futuro)
    return pob_futura

# Años futuros
años_futuros = [2025, 2026, 2027]

# Proyección
proj_mazatlan = proyectar_poblacion(t, denue_villa_anual, años_futuros)

# Resultado
df_proy = pd.DataFrame({
    'Fecha de incorporación': años_futuros,
    'Cantidad': proj_mazatlan.round(0).astype(int)
})

# Unir los dos DataFrames
df_denue_completa = pd.concat([fecha_denue, df_proy], ignore_index=True)
df_denue_completa


In [ ]:
# Calculareos en donde se centra la mayoria de las personas en la zona de estuido 

# Calculamos el número de DENUES que tiene de 0 a 5 personas empleadas hasta los 251 y más
personal_ocupado_dataframe = denue_c['Descripcion estrato personal ocupado'].value_counts().reset_index()

# Pasamos los reultados a un DataFrame
personal_ocupado_dataframe.columns = ["Descripcion estrato personal ocupado", 'Cantidad']

# Promediamos el númerp de personas empleadas por tamaño del DENUE
datos = [2.5,
         8,
         20.5,
         40.5,
         75.5,
         175.5]

# Calculamos la cantida de personas por tamaño de DENUE
personal_ocupado_dataframe["Número de personas"] = personal_ocupado_dataframe["Cantidad"] * datos
# Calculamos el total de personas empleadas en la zona 
suma_ocupa = personal_ocupado_dataframe["Número de personas"].sum()

# Agregar la columna de porcentaje
personal_ocupado_dataframe["Porcentaje"] = (personal_ocupado_dataframe["Número de personas"] / suma_ocupa) * 100

# Ordenemos de Mayor a menor 
personal_ocupado_dataframe = personal_ocupado_dataframe.sort_values(by='Porcentaje', ascending=False)

# Agregar la columna de porcentaje acumulado
personal_ocupado_dataframe["Porcentaje Acumulado"] = personal_ocupado_dataframe["Porcentaje"].cumsum()
personal_ocupado_dataframe


### Analisis Negocios en Google

In [ ]:
'''
# Coordenadas Villa Unión
coordenadas = (23.18921971267745, -106.21486725615958)  
# Radio de busqueda en Kilometros 
r = 3

# Llamamos la funcion para obtener la base de comercios en la zona
base_datos= obtener_establecimientos_localidad(coordenadas, comercios,r)
base_datos.drop('ID', axis=1, inplace=True)

# Invertir el diccionario para hacer la búsqueda más eficiente
mapa_establecimientos = {establecimiento: categoria for categoria, lista in categorias_establecimientos.items() for establecimiento in lista}

# Agregar la categoría al DataFrame
base_datos['Categoría de establecimiento'] = base_datos['Establecimiento'].map(mapa_establecimientos)

# Mover la columna 'C' a la primera posición (índice 0)
col = base_datos.pop('Categoría de establecimiento')  # Extraer la columna
base_datos.insert(2, 'Categoría de establecimiento', col)

# Eliminar duplicados basándose solo en 'Nombre de establecimiento'
df_sin_duplicados = base_datos.drop_duplicates(subset=['Nombre de establecimiento'], keep='first') 


# Tipo de establecimiento
df_establecimiento = df_sin_duplicados['Establecimiento'].value_counts().reset_index()
df_establecimiento.columns = ['Establecimiento', 'Cantidad']

# Categoria de establecimientos
df_categorias = df_sin_duplicados['Categoría de establecimiento'].value_counts().reset_index()
df_categorias.columns = ['Categoría de establecimiento', 'Cantidad']


# Guardar el resultado en un csv
df_sin_duplicados.to_csv("Comercios Villa Union.csv", index=False, encoding='utf-8-sig')
# Guardar el resultado en un csv
df_establecimiento.to_csv("Tipo de comercions en Villa Union.csv", index=False, encoding='ISO-8859-1')
# Guardar el resultado en un csv
df_categorias.to_csv("Categoria de comercios Villa Union.csv", index=False, encoding='ISO-8859-1')

'''


In [ ]:

df_sin_duplicados = leer_archivo("Comercios Villa Union.csv")

# Crear un mapa centrado en un punto de la plaza
mapa = folium.Map(location=[df_sin_duplicados['latitud'].mean(), df_sin_duplicados['longitud'].mean()], zoom_start=16)

# Añadir los establecimientos al mapa
for index, row in df_sin_duplicados.iterrows():
    folium.Marker([row['latitud'], row['longitud']], popup=row['Nombre de establecimiento']).add_to(mapa)

# Guardar Mapa
mapa.save("Comercios Villa Unión por google maps.html")
mapa